## Determining CpG ratio per Gene Function
## in the Geoduck data.
### Files needed
GO-slim with unique data

"analyses/Geoduck-transcriptome-v2-GO-SlimUnique.csv"

fasta file with contigs

"analyses/Geoduck-transcriptome-v2.fasta"

### Importing libraries

In [1]:
from Bio import SeqIO
from pandas import Series, DataFrame
import pandas as pd
import pylab
from Bio.SeqUtils import GC
import matplotlib.pyplot as plt
import numpy as np
import pylab as pl
from pylab import *
import numpy as np

Checking working directory and files

In [2]:
!pwd

/Users/migueldelrio/Desktop/panopea/panopea_data


In [3]:
!ls analyses/

Dheilly-Fastafile_Microarray.fa
Dheilly-Microarray.nhr
Dheilly-Microarray.nin
Dheilly-Microarray.nsq
Dheilly_Geo_blast_analises.xlsx
Dheilly_blastx_Geoduck.out
Geo-pep_tblastn_Dheilly.out
Geo_blast_BacteriaEukaryota.xlsx
Geoduck-transcriptome-v2-GO-SlimUnique.csv
Geoduck-transcriptome-v2.fasta
Geoduck-transcriptome-v2.nhr
Geoduck-transcriptome-v2.nin
Geoduck-transcriptome-v2.nsq
Geoduck-transcriptome-v3
Geoduck-tranv2-blastx_sprot.sorted
Geoduck-tranv2-minus_direction.tab
Geoduck-tranv3-blastx_sprot.sorted
Geoduck-v2-GOslim_only%.txt
Geoduck-v2-GOslim_only.sorted
Geoduck-v2-GOslim_only.txt
Geoduck-v2-protein.phr
Geoduck-v2-protein.pin
Geoduck-v2-protein.psq
Geoduck-v3_blastn_Cgigas_cdna.out
Geoduck-v3_blastn_Cgigas_cdna_e10.out
Geoduck-v3_blastn_GIGAton_e10.out
Geoduck-v3_blastn_RuphiBase.out
Geoduck-v3_blastn_RuphiBase_e10.out
Geoduck-v3_blastn_RuphiBase_e10.xlsx
Geoduck-v3_blastn_RuphiBase_e60.out
Geoduck-v3_blastn_RuphiBase_e60.xlsx
Geoduck-v3_blastn_RuphiBase_out.xlsx
Geoduck_v2_bl

In [4]:
!head "analyses/Geoduck-transcriptome-v2-GO-SlimUnique.csv"

comp141380_c2_seq35,sp,Q9H295,D^C


## Step 1: Obtaining GO slim information (gene function)

In [5]:
f = pd.read_csv('analyses/Geoduck-transcriptome-v2-GO-SlimUnique.csv')

Create a temporary dataframe *f1* with the sequence 'id' and its 'GOSlim_bin'

In [6]:
f1=DataFrame({'id':f['Column1'],'GOSlimbin': f['GOSlim_bin']})
f1=f1.sort('id')
f1

GOSlimbin                  id
4145                         transport  comp100097_c0_seq1
4146                protein metabolism  comp100104_c2_seq1
4147                    RNA metabolism  comp100105_c1_seq1
4148                         transport  comp100108_c1_seq1
4149        other biological processes  comp100109_c0_seq1
4150        other biological processes  comp100113_c0_seq1
4152                protein metabolism  comp100113_c0_seq2
4151                protein metabolism  comp100113_c1_seq1
4153        other biological processes  comp100129_c0_seq1
4154         other metabolic processes  comp100141_c0_seq1
4155                protein metabolism  comp100174_c1_seq1
4156                             death  comp100184_c0_seq2
4157        other biological processes  comp100187_c0_seq1
4158         other metabolic processes  comp100218_c0_seq1
4159                protein metabolism  comp100298_c0_seq1
4160         other metabolic processes  comp100305_c0_seq1
4161         other metabolic processes  comp100366_c1_seq1
4162                         transport  comp100370_c0_seq1
4163        other biological processes  comp100414_c0_seq1
4164                    RNA metabolism  comp100414_c1_seq1
4165                         transport  comp100439_c1_seq1
4166        other biological processes  comp100440_c0_seq1
4167         other metabolic processes  comp100442_c0_seq1
4168        other biological processes  comp100466_c0_seq1
4169           developmental processes  comp100480_c0_seq1
4170         other metabolic processes  comp100480_c1_seq1
4171         other metabolic processes  comp100502_c1_seq1
4172                             death  comp100517_c1_seq1
4173         other metabolic processes  comp100523_c0_seq1
4174         other metabolic processes  comp100540_c0_seq1
...                                ...                 ...
4116         other metabolic processes   comp99577_c1_seq1
4117         other metabolic processes   comp99584_c0_seq1
4118                protein metabolism   comp99603_c0_seq1
4119        other biological processes   comp99604_c1_seq1
4120  cell organization and biogenesis   comp99640_c0_seq2
4121                    RNA metabolism   comp99698_c0_seq1
4122         other metabolic processes   comp99725_c0_seq1
4123         other metabolic processes   comp99725_c0_seq2
4124         other metabolic processes   comp99731_c0_seq1
4125        other biological processes   comp99768_c1_seq1
4126         other metabolic processes   comp99776_c0_seq1
4127                         transport   comp99786_c0_seq1
4128                         transport   comp99794_c0_seq1
4129                    RNA metabolism   comp99807_c0_seq1
4130         other metabolic processes   comp99818_c0_seq1
4131        other biological processes   comp99849_c0_seq1
137                     RNA metabolism    comp9984_c0_seq1
4132                protein metabolism   comp99866_c0_seq1
4133                         transport   comp99880_c0_seq1
4134                    RNA metabolism   comp99891_c0_seq1
4136                protein metabolism   comp99895_c0_seq1
4135                protein metabolism   comp99895_c0_seq2
4137                protein metabolism   comp99916_c0_seq1
4139                             death   comp99943_c0_seq1
4138                             death   comp99943_c1_seq2
4140                protein metabolism   comp99950_c0_seq1
4141               signal transduction   comp99983_c1_seq1
4142                   stress response   comp99986_c2_seq1
4144                protein metabolism   comp99996_c0_seq1
4143                protein metabolism   comp99996_c2_seq1

[19652 rows x 2 columns]

## step 2 reading fasta file

In [7]:
# fasta file to calculate the CpG content per contig
handle = "analyses/Geoduck-transcriptome-v2.fasta"

### using biopython fasta file management and routines to count "C", "G" and "CG, together with the sequence length
### calculates CpG 

Creates temporary variables

In [8]:
record_id = []
record_cpg = []
for record in SeqIO.parse(handle, "fasta"):
    g= record.seq.count("G")
    c= record.seq.count("C")
    cg= record.seq.count("CG")
    lar= len(record.seq)
    try:
        g*c==0
    except:
        print (record.id)
        record_id.append(record.id)
        record_cpg.append(0.0000)
    else:
        print (record.id, round(cg/(g*c)*(lar**2/(lar-1)) ,4))
        record_id.append(record.id)
        record_cpg.append(round(cg/(g*c)*(lar**2/(lar-1)) ,4))

comp7_c0_seq1 1.3882
comp30_c0_seq1 0.9665
comp35_c0_seq1 0.6306
comp36_c0_seq1 0.0
comp49_c0_seq1 0.837
comp59_c0_seq1 0.5102
comp60_c0_seq1 0.2415
comp65_c0_seq1 0.3077
comp66_c0_seq1 0.7564
comp69_c0_seq1 0.4943
comp71_c0_seq1 0.4552
comp90_c0_seq1 0.1674
comp93_c0_seq1 1.1423
comp95_c0_seq1 0.6196
comp105_c0_seq1 0.6544
comp115_c0_seq1 0.6782
comp117_c0_seq1 0.0
comp128_c0_seq1 0.325
comp135_c0_seq1 0.0
comp137_c0_seq1 0.7535
comp142_c0_seq1 0.1629
comp146_c0_seq1 1.2283
comp148_c0_seq1 0.3136
comp171_c0_seq1 1.4192
comp171_c0_seq2 1.3113
comp176_c0_seq1 0.1412
comp177_c0_seq1 1.1289
comp178_c0_seq1 0.7138
comp182_c0_seq1 0.6048
comp190_c0_seq1 1.0541
comp195_c0_seq1 0.9776
comp216_c0_seq1 1.0158
comp217_c0_seq1 0.3013
comp234_c0_seq1 0.0
comp235_c0_seq1 0.357
comp242_c0_seq1 1.409
comp246_c0_seq1 0.0
comp250_c0_seq1 0.7553
comp259_c0_seq1 1.3844
comp268_c0_seq1 0.8356
comp275_c0_seq1 0.1819
comp277_c0_seq1 0.2047
comp277_c1_seq1 0.2581
comp279_c0_seq1 0.1171
comp282_c0_seq1 0.2003

### Uses temporary variables to obtain the CpG and sequence.id as a dataframe, which will be used later

In [9]:
records = DataFrame({'id':record_id, 'CpG':record_cpg})
records = records.sort('id')
records

CpG                  id
37873  0.9190  comp100000_c0_seq1
37874  0.2642  comp100001_c1_seq1
37875  0.2336  comp100001_c2_seq1
37876  0.9859  comp100002_c0_seq1
37877  0.4392  comp100004_c1_seq1
37878  0.6894  comp100007_c0_seq1
37879  1.1367  comp100010_c0_seq1
37880  0.5625  comp100011_c0_seq1
37881  0.1521  comp100012_c0_seq1
37882  0.5719  comp100014_c0_seq1
37883  1.0333  comp100015_c0_seq1
37884  0.9937  comp100025_c0_seq1
37885  0.3348  comp100027_c1_seq1
37886  0.6695  comp100029_c1_seq1
37887  0.3333  comp100031_c0_seq1
37888  0.6545  comp100033_c0_seq1
37889  0.2124  comp100035_c0_seq1
37890  0.1133  comp100036_c0_seq1
37891  0.3425  comp100036_c0_seq2
37892  0.3147  comp100038_c0_seq1
1880   0.5952   comp10003_c0_seq1
37893  0.2485  comp100041_c0_seq1
37894  0.6736  comp100041_c1_seq1
37895  0.4449  comp100041_c1_seq2
37896  0.4476  comp100043_c0_seq1
37897  0.8793  comp100045_c0_seq1
37898  0.2943  comp100046_c1_seq1
37899  0.4034  comp100047_c0_seq1
37900  0.8391  comp100047_c0_seq2
37901  0.8274  comp100052_c0_seq1
...       ...                 ...
37843  0.3205   comp99952_c0_seq2
37844  1.1684   comp99956_c0_seq1
37845  0.4704   comp99957_c0_seq1
37846  0.5920   comp99964_c0_seq1
37847  0.0000   comp99965_c0_seq1
37848  0.2637   comp99966_c0_seq1
37849  0.8711   comp99967_c0_seq1
37850  0.3781   comp99970_c0_seq1
37851  0.4493   comp99971_c0_seq1
37852  0.1716   comp99972_c0_seq1
37853  0.2049   comp99972_c0_seq2
37854  1.2461   comp99973_c0_seq1
37855  0.4504   comp99974_c0_seq1
37856  0.8655   comp99979_c0_seq1
37857  1.0585   comp99980_c0_seq1
37858  0.9778   comp99980_c0_seq2
37859  0.7030   comp99982_c0_seq1
37860  0.3717   comp99983_c0_seq1
37861  0.5735   comp99983_c1_seq1
37862  0.1122   comp99984_c0_seq1
37863  0.6521   comp99985_c0_seq1
37864  0.6468   comp99986_c0_seq1
37865  0.4332   comp99986_c2_seq1
37866  0.7005   comp99988_c0_seq1
37867  0.8134   comp99988_c0_seq2
37868  0.4897   comp99991_c0_seq1
37869  0.1679   comp99995_c0_seq1
37870  1.3065   comp99996_c0_seq1
37871  1.1719   comp99996_c2_seq1
37872  0.5837   comp99998_c0_seq1

[154407 rows x 2 columns]

In [10]:
records.describe()

CpG
count  154407.000000
mean        0.549013
std         0.324474
min         0.000000
25%         0.323900
50%         0.492900
75%         0.730000
max         3.514300

### Joints temporary dataframes into a single dataframe and saves csv file

In [11]:
f2=pd.merge(f1,records, how='outer')
f2

GOSlimbin                  id     CpG
0                        transport  comp100097_c0_seq1  0.4868
1               protein metabolism  comp100104_c2_seq1  0.5637
2                   RNA metabolism  comp100105_c1_seq1  0.5038
3                        transport  comp100108_c1_seq1  0.5092
4       other biological processes  comp100109_c0_seq1  0.6331
5       other biological processes  comp100113_c0_seq1  1.1629
6               protein metabolism  comp100113_c0_seq2  0.9827
7               protein metabolism  comp100113_c1_seq1  1.4217
8       other biological processes  comp100129_c0_seq1  0.3669
9        other metabolic processes  comp100141_c0_seq1  0.3492
10              protein metabolism  comp100174_c1_seq1  1.0979
11                           death  comp100184_c0_seq2  0.6362
12      other biological processes  comp100187_c0_seq1  0.4943
13       other metabolic processes  comp100218_c0_seq1  0.4302
14              protein metabolism  comp100298_c0_seq1  0.8889
15       other metabolic processes  comp100305_c0_seq1  0.3136
16       other metabolic processes  comp100366_c1_seq1  0.3753
17                       transport  comp100370_c0_seq1  1.0658
18      other biological processes  comp100414_c0_seq1  0.7530
19                  RNA metabolism  comp100414_c1_seq1  0.5537
20                       transport  comp100439_c1_seq1  0.6720
21      other biological processes  comp100440_c0_seq1  0.3251
22       other metabolic processes  comp100442_c0_seq1  1.2525
23      other biological processes  comp100466_c0_seq1  0.4346
24         developmental processes  comp100480_c0_seq1  0.7456
25       other metabolic processes  comp100480_c1_seq1  0.4475
26       other metabolic processes  comp100502_c1_seq1  0.8691
27                           death  comp100517_c1_seq1  0.4501
28       other metabolic processes  comp100523_c0_seq1  1.0283
29       other metabolic processes  comp100540_c0_seq1  0.6182
...                            ...                 ...     ...
154377                         NaN   comp99949_c0_seq1  0.4125
154378                         NaN   comp99951_c0_seq1  0.4868
154379                         NaN   comp99951_c1_seq1  0.1961
154380                         NaN   comp99952_c0_seq1  0.3434
154381                         NaN   comp99952_c0_seq2  0.3205
154382                         NaN   comp99956_c0_seq1  1.1684
154383                         NaN   comp99957_c0_seq1  0.4704
154384                         NaN   comp99964_c0_seq1  0.5920
154385                         NaN   comp99965_c0_seq1  0.0000
154386                         NaN   comp99966_c0_seq1  0.2637
154387                         NaN   comp99967_c0_seq1  0.8711
154388                         NaN   comp99970_c0_seq1  0.3781
154389                         NaN   comp99971_c0_seq1  0.4493
154390                         NaN   comp99972_c0_seq1  0.1716
154391                         NaN   comp99972_c0_seq2  0.2049
154392                         NaN   comp99973_c0_seq1  1.2461
154393                         NaN   comp99974_c0_seq1  0.4504
154394                         NaN   comp99979_c0_seq1  0.8655
154395                         NaN   comp99980_c0_seq1  1.0585
154396                         NaN   comp99980_c0_seq2  0.9778
154397                         NaN   comp99982_c0_seq1  0.7030
154398                         NaN   comp99983_c0_seq1  0.3717
154399                         NaN   comp99984_c0_seq1  0.1122
154400                         NaN   comp99985_c0_seq1  0.6521
154401                         NaN   comp99986_c0_seq1  0.6468
154402                         NaN   comp99988_c0_seq1  0.7005
154403                         NaN   comp99988_c0_seq2  0.8134
154404                         NaN   comp99991_c0_seq1  0.4897
154405                         NaN   comp99995_c0_seq1  0.1679
154406                         NaN   comp99998_c0_seq1  0.5837

[154407 rows x 3 columns]

# file save as csv 

In [12]:
f2.to_csv('analyses/Geoduck-transcriptome-CpG_GOSlim.csv')

### Plotting

In [13]:
f2['CpG'].hist()
show()

In [14]:
f2.groupby('GOSlimbin')['CpG'].mean().plot(kind='barh', color=list('ybg'))
plt.axis([0.4, 0.7, 0, 15])
show()

![TEKTA1](img/figure_1histo.png)

In [15]:
# pandas density plot
f2['CpG'].plot(kind='kde', linewidth=3);
plt.axis([0, 1.5, 0, 1.9])
show()

![TEKTA1](img/figure_1dens.png)